### Testing Jordan's idea for plotting alignability on a single coordinate system, starting with chr11 subgroup C

In [1]:
## import statements
import os
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import glob
import re
from collections import defaultdict

In [2]:
cigar_path="/private/groups/patenlab/mira/centrolign/batch_submissions/centrolign/release2_QC_v2/MSA/chr11/subgroup_C/induced_pairwise_cigars/"
fai="/private/groups/patenlab/mira/centrolign/batch_submissions/centrolign/release2_QC_v2/split_nj_trees/chr11/combine_final_subgroups/chr11.subgroup_C.fasta.fai"

In [3]:
# Parse fai file into a dataframe of sample, asat length
smp_lengths = pd.read_csv(
    fai,
    sep="\t",
    header=None,
    usecols=[0, 1],       # only contig and length
    names=["sample", "length"]
)

In [6]:
# This function will take in the length of the array, and current base position, and return the new position normalized between 0 and 1 
def normalize(position, length):
    if length == 1:
        return 0.0  # avoid divide by zero
    return (position - 1) / (length - 1)

In [27]:
## Functions to parse cigar, and reverse cigar
def parse_cigar(cigar):
    parsed = []
    for m in re.finditer("(\d+)([HSMIDX=])", cigar):
        parsed.append((m.group(2), int(m.group(1))))
    return parsed

def reverse_cigar(parsed):
    for i in range(len(parsed)):
        if parsed[i][0] == "I":
            parsed[i] = ("D", parsed[i][1])
        elif parsed[i][0] == "D":
            parsed[i] = ("I", parsed[i][1])
    return parsed

def map_to_samples(fps):
    suff_regex = r"([A-Za-z0-9]+\.[0-9]+)_([A-Za-z0-9]+\.[0-9]+)\.txt$"

    sample_map = {}
    for fp in fps:
        fname = os.path.basename(fp)
        m = re.search(suff_regex, fname)
        assert m is not None, f"Regex failed for file: {fname}"
        key = (m.group(1), m.group(2))
        sample_map[key] = fp
        #print("Added:", key, "->", fp)

    print("Final sample_map:", sample_map)
    return sample_map


<>:4: SyntaxWarning: "\d" is an invalid escape sequence. Such sequences will not work in the future. Did you mean "\\d"? A raw string is also an option.
<>:4: SyntaxWarning: "\d" is an invalid escape sequence. Such sequences will not work in the future. Did you mean "\\d"? A raw string is also an option.
/data/tmp/ipykernel_3561018/383950167.py:4: SyntaxWarning: "\d" is an invalid escape sequence. Such sequences will not work in the future. Did you mean "\\d"? A raw string is also an option.
  for m in re.finditer("(\d+)([HSMIDX=])", cigar):


In [21]:
## Create list of proportion of aligned coverage at every base in reference cigar string

def per_base_alignment_proportion(cigars):
    '''
    Takes in a nested list of cigar strings all aligned to a single reference 
    Returns a list of proportion aligned at every base, where index = base position in array
    '''
    # Build coverage dictionary mapping ref_pos → count of aligned M/= /X
    coverage = defaultdict(int)
    print(cigars)
    for cigar in cigars:
        ref_pos = 0
        
        for op, length in cigar:
            if op in ("M", "=", "X"):
                for _ in range(length):
                    coverage[ref_pos] += 1
                    ref_pos += 1
            elif op == "D":
                # consumes ref but is not counted as aligned
                ref_pos += length
            else:
                # I, S, H do NOT consume ref
                continue
    print(coverage)
    # Find reference length
    max_ref_pos = max(coverage.keys()) + 1

    total = len(cigars)
    proportions = [coverage[pos] / total for pos in range(max_ref_pos)]
    return proportions

In [31]:
def map_to_samples(fps):
    suff_regex = r"([A-Za-z0-9]+\.[0-9]+)_([A-Za-z0-9]+\.[0-9]+)\.txt$"

    sample_map = {}
    for fp in fps:
        print("\nProcessing:", fp)
        fname = os.path.basename(fp)
        m = re.search(suff_regex, fname)
        print("  regex match:", m)

        if m is None:
            raise ValueError(f"Regex failed for file: {fname}")

        print("  group1:", m.group(1))
        print("  group2:", m.group(2))

        key = (m.group(1), m.group(2))
        print("  key:", key)

        print("  storing in map...")
        sample_map[key] = fp

        print("  sample_map now:", sample_map)

    print("\nFinal sample_map:", sample_map)
    return sample_map



In [ ]:
# get list of cigar strings for chr 11 subgroup C 
cigar_files = [os.path.join(cigar_path, f) for f in os.listdir(cigar_path) if f.startswith("pairwise_cigar_")]
print(len(cigar_files))
# get dictionary of [ref,query]:filepath for all cigar strings in 
existing_cigar_sample_map = map_to_samples(cigar_files)

print(existing_cigar_sample_map)
# sample_list = smp_lengths['sample'].tolist()
# proportions=[]



In [45]:
for sample in sample_list:
    print("Processing sample:", sample)
    
    pairs = [(sample, other) for other in sample_list if other != sample]
    sample_cigars = []

    print("Num cigars found:", len(cigar_files))
    print("Map contents:", existing_cigar_sample_map)
    print("Sample list:", sample_list)

    for pair in pairs:

        if pair not in existing_cigar_sample_map:
            rev_pair = (pair[1], pair[0])
            print(rev_pair in existing_cigar_sample_map)
            assert rev_pair in existing_cigar_sample_map, f"{rev_pair} not in map!"
            with open(existing_cigar_sample_map[rev_pair], "r") as f:
                r_cigar = parse_cigar(f.read())
            direct_cigar = reverse_cigar(r_cigar)
        else:
            with open(existing_cigar_sample_map[pair], "r") as f:
                direct_cigar = parse_cigar(f.read())

        sample_cigars.append(direct_cigar)

    print("Cigars collected:", sample_cigars)

    proportions = per_base_alignment_proportion(sample_cigars)
    print("Proportions:", proportions)
    break

print("hello")

print("hello")

Processing sample: CHM13.0
Num cigars found: 7503
Map contents: {('NA20346.1', 'NA18505.1'): '/private/groups/patenlab/mira/centrolign/batch_submissions/centrolign/release2_QC_v2/MSA/chr11/subgroup_C/induced_pairwise_cigars/pairwise_cigar_NA20346.1_NA18505.1.txt', ('HG00320.2', 'NA19185.1'): '/private/groups/patenlab/mira/centrolign/batch_submissions/centrolign/release2_QC_v2/MSA/chr11/subgroup_C/induced_pairwise_cigars/pairwise_cigar_HG00320.2_NA19185.1.txt', ('HG02273.2', 'NA21106.2'): '/private/groups/patenlab/mira/centrolign/batch_submissions/centrolign/release2_QC_v2/MSA/chr11/subgroup_C/induced_pairwise_cigars/pairwise_cigar_HG02273.2_NA21106.2.txt', ('HG03816.2', 'HG03139.1'): '/private/groups/patenlab/mira/centrolign/batch_submissions/centrolign/release2_QC_v2/MSA/chr11/subgroup_C/induced_pairwise_cigars/pairwise_cigar_HG03816.2_HG03139.1.txt', ('HG02258.1', 'HG00350.1'): '/private/groups/patenlab/mira/centrolign/batch_submissions/centrolign/release2_QC_v2/MSA/chr11/subgroup_C/

KeyboardInterrupt: 